# Checking if GPU is connected:


In [2]:
!nvidia-smi


Fri Mar 22 19:30:16 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla V100-SXM2-16GB           Off | 00000000:00:04.0 Off |                    0 |
| N/A   35C    P0              23W / 300W |      0MiB / 16384MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

# Installing the required packages

In [3]:
!pip install --upgrade diffusers[torch]
!pip install number-parser


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 1.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 290.1/290.1 kB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 1.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 2.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 1.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 1.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 1.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 1.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 166.0/166.0 MB 1.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━

# Importing the required packages

In [4]:
import pandas as pd
import numpy as np
import torch
from diffusers import StableDiffusionPipeline
import os
import string
import re
import nltk
from nltk.tokenize import word_tokenize
nltk.download('punkt')
from collections import defaultdict
from number_parser import parse_number

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


# Giving colab access to my drive to access the dataframe and save images

In [5]:
from google.colab import drive # connecting to my drive
drive.mount('/content/drive')


Mounted at /content/drive


# Setting my directory in drive using os

In [6]:
os.chdir('/content/drive/My Drive/Big-Foot/Assignment_2/Scripts/task5') # setting chdir, this is where my script is located

# Reading in the dataframe from assignment 1

In [29]:
df = pd.read_csv("../../Data/reports_v2.tsv", sep="\t") # reading in the df from assignment 1

print(df)

        Report Type     Id    Class                Submitted Date  \
0            Report  13038  Class A  Saturday, November 12, 2005.   
1            Report   8792  Class B       Thursday, June 3, 2004.   
2            Report   1255  Class B     Tuesday, October 5, 1999.   
3     Media Article    658      NaN   Wednesday, January 23, 2013   
4            Report  11616  Class B          Friday, May 6, 2005.   
...             ...    ...      ...                           ...   
5462         Report   1411  Class A    Tuesday, January 23, 2001.   
5463  Media Article     59      NaN      Wednesday, June 18, 1980   
5464         Report  14714  Class A         Friday, May 19, 2006.   
5465         Report  12884  Class A    Tuesday, October 25, 2005.   
5466         Report    798  Class B        Monday, June 26, 2000.   

                                               Headline  Year  Season  \
0     Snowmobiler has encounter in deep snow near Po...  2004  Winter   
1     Four nocturnal hike

# Leveraging and combining text from selected sighting columns
Note: I sected these based on importance. The image generator can only take 77 tokens so for the first round I wanted to be selective. For sightings with less text, I later add more columns.

In [30]:
# defining a list of columns to merge
#columns_to_leverage = ['Observed', 'Observed.1', 'Also Noticed', 'Environment', 'Time And Conditions', 'Location Details']
columns_to_leverage = ['Observed', 'Observed.1','Environment', 'Time And Conditions', 'Season']
# headline?
# season

# joining sentences from text column into one image descriotion column
# if nan value leave out
df['Image Text'] = df[columns_to_leverage].apply(lambda x: '. '.join(str(val) for val in x if not pd.isna(val)) + '.' if str(x[-1])[-1] != '.' else '. '.join(str(val) for val in x if not pd.isna(val)), axis=1)
# then adding witness count as a sentence to the end
df['Image Text'] = df['Image Text'] + df['Witness Count'].astype(str) + ' witnesses.'

print(df['Image Text'])
print("")


# print(df['Image Text'].loc[0])


0       I and two of my friends were bored one night s...
1       Me and a couple of friends had been bored, whe...
2       My hunting buddy and I were sitting on a ridge...
3       Here is the original sketch of the creature wi...
4       To whom it may concern, I am a commercial fish...
                              ...                        
5462    On 6-94 we visited Yellowstone National Park a...
5463    The two men said that they were going to visit...
5464    I was delivering newspapers on a lightly snowi...
5465    I was 19 years old at that time. I had just go...
5466    I am not sure how relevant this report will be...
Name: Image Text, Length: 5467, dtype: object



# Preprocess Image Text to remove punctuation, special characters, and convert to lowercase for tokenization

In [31]:
def preprocess_text(text):
    # remove punctuation
    text = text.translate(str.maketrans('', '', string.punctuation))

    # convert to lowercase
    text = text.lower()

    # handle special characters
    text = re.sub(r'[^a-zA-Z0-9\s]', '', text)

    return text


# apply preprocessing to each row in the 'Image Text' column to reduce tokens
df['Image Text'] = df['Image Text'].apply(preprocess_text)

print(df['Image Text'])

0       i and two of my friends were bored one night s...
1       me and a couple of friends had been bored when...
2       my hunting buddy and i were sitting on a ridge...
3       here is the original sketch of the creature wi...
4       to whom it may concern i am a commercial fishe...
                              ...                        
5462    on 694 we visited yellowstone national park an...
5463    the two men said that they were going to visit...
5464    i was delivering newspapers on a lightly snowi...
5465    i was 19 years old at that time i had just got...
5466    i am not sure how relevant this report will be...
Name: Image Text, Length: 5467, dtype: object


# Further preprocessing the text by attempting to convert simple cases of numbers to words using number parser and removing multi digit numbers
Note: The image generator seems to tokenize multi-digit numbers by splitting them into separate digits which is why I am doing this to attempt to get my 77 token count closer to how the image generator counts tokens.

In [32]:
# the image generator seems like it separates each digit in a number and counts it like a separate token
# to try to mitiage this I am using parse-number for easy cases of converting numbers to words
def parse_numbers_in_string(text):
    # split the string into words
    words = text.split()

    # parse each word that represents a number
    parsed_words = [str(parse_number(word)) if word.isdigit() else word for word in words]

    # remove multi digit numbers as they are split into separate tokens bu diffusers
    text_no_multi_digits = ' '.join([word for word in parsed_words if not re.match(r'\b\d{2,}\b', word)])

    return text_no_multi_digits

# apply the function to each row
df['Image Text'] = df['Image Text'].apply(parse_numbers_in_string)

print(df['Image Text'])

0       i and two of my friends were bored one night s...
1       me and a couple of friends had been bored when...
2       my hunting buddy and i were sitting on a ridge...
3       here is the original sketch of the creature wi...
4       to whom it may concern i am a commercial fishe...
                              ...                        
5462    on we visited yellowstone national park and re...
5463    the two men said that they were going to visit...
5464    i was delivering newspapers on a lightly snowi...
5465    i was years old at that time i had just gotten...
5466    i am not sure how relevant this report will be...
Name: Image Text, Length: 5467, dtype: object


# Tokenize the Image Text and select 77 tokens per row

In [33]:
# keywords to prioritize
priority_keywords = ["bigfoot", "creature", "animal", "hairy", "hair", "print", "noise", "noisy", "it", "scared"]

# tokenize the text
def tokenize_text(text):
  return word_tokenize(text.lower())

# extract tokens within a window around the word "creature" and prioritize based on keywords
def prioritize_tokens(tokens):
    if len(tokens) <= 77:
      # print(len(tokens))
      return tokens
    priority_words = ["bigfoot", "creature", "animal"]
    for word in priority_words:
        if word in tokens:
            center_word = word
            center_index = tokens.index(center_word)
            window_size = 77
            start_index = max(0, center_index - window_size // 2)
            end_index = min(len(tokens), center_index + window_size // 2 + 1)
            extracted_tokens = tokens[start_index:end_index]
            # print(len(extracted_tokens))
            return extracted_tokens
            if end_index - start_index < 77:
                if start_index < 38:
                  start_index = 0
                  end_index = min(len(tokens), start_index + 77)
                else:
                  start_index = max(0, len(tokens) - 77)
                  end_index = len(tokens)
            extracted_tokens = tokens[start_index:end_index]
            # print(len(extracted_tokens))
            return extracted_tokens
    # if no priority words found, extract 77 tokens from the middle of the list
    start_index = max(0, len(tokens) // 2 - 38)
    end_index = min(len(tokens), start_index + 77)
    extracted_tokens = tokens[start_index:end_index]
    # print(len(extracted_tokens))
    return extracted_tokens

# Apply tokenization and prioritization to each row in the DataFrame
for index, row in df.iterrows():
    tokens = tokenize_text(row['Image Text'])
    priority_tokens = prioritize_tokens(tokens)
    # print(len(priority_tokens))
    df.at[index, 'Image Text'] = priority_tokens


print(df['Image Text'])

0       [my, friends, were, bored, one, night, so, we,...
1       [for, mushers, runners, cross, country, skiier...
2       [hour, move, from, one, tree, accross, the, cl...
3       [riding, their, 4wheeler, when, they, saw, it,...
4       [fishing, i, try, to, take, a, trip, up, river...
                              ...                        
5462    [man, its, stride, was, long, with, its, arms,...
5463    [the, two, men, said, that, they, were, going,...
5464    [it, didnt, seem, to, be, bothered, by, the, c...
5465    [job, with, a, seismographic, company, my, cou...
5466    [i, am, not, sure, how, relevant, this, report...
Name: Image Text, Length: 5467, dtype: object


# Converting Image Text back to string

In [34]:
# converting back to string and removing punctuation
df['Image Text'] = df['Image Text'].apply(str).apply(preprocess_text)
print(df['Image Text'])

0       my friends were bored one night so we decided ...
1       for mushers runners cross country skiiers and ...
2       hour move from one tree accross the clearing t...
3       riding their 4wheeler when they saw it it was ...
4       fishing i try to take a trip up river with a f...
                              ...                        
5462    man its stride was long with its arms swinging...
5463    the two men said that they were going to visit...
5464    it didnt seem to be bothered by the cold or th...
5465    job with a seismographic company my cousin als...
5466    i am not sure how relevant this report will be...
Name: Image Text, Length: 5467, dtype: object


# Adding in additional text columns and repeating preprocessing steps for rows with less than 77 tokens from the original selection

In [35]:
# check which rows have less than 77 tokens
for index, row in df.iterrows():
    text = row['Image Text']
    token_count = len(tokenize_text(text))
    #print(f"Token Count: {token_count}")
    if token_count < 77:
      # join addition text cols i initially left out where the token count is less than 77
      updated_text = ' '.join([str(row[col]) for col in ['Also Noticed', 'Headline', 'Time And Conditions', 'Location Details'] if not pd.isna(row[col])])
      df.at[index, 'Image Text'] = updated_text
      #print(f"Index: {index}, Text: {text}, Token Count: {token_count}")


# calling the prior preprocess & tokenization functions on the updated column
df['Image Text'] = df['Image Text'].apply(preprocess_text)
df['Image Text'] = df['Image Text'].apply(parse_numbers_in_string)

for index, row in df.iterrows():
    tokens = tokenize_text(row['Image Text'])
    priority_tokens = prioritize_tokens(tokens)
    # print(len(priority_tokens))
    df.at[index, 'Image Text'] = priority_tokens

df['Image Text'] = df['Image Text'].apply(str).apply(preprocess_text)


print(df['Image Text'])



0       my friends were bored one night so we decided ...
1       for mushers runners cross country skiiers and ...
2       hour move from one tree accross the clearing t...
3       riding their 4wheeler when they saw it it was ...
4       fishing i try to take a trip up river with a f...
                              ...                        
5462    man its stride was long with its arms swinging...
5463            two men report seeing huge hairy creature
5464    it didnt seem to be bothered by the cold or th...
5465    job with a seismographic company my cousin als...
5466    nothing car passenger sees figure on road on r...
Name: Image Text, Length: 5467, dtype: object


# Generating Images: Initializing the Diffusion Pipeline

In [14]:
# initializing diffusion pipeline
pipeline = StableDiffusionPipeline.from_pretrained("runwayml/stable-diffusion-v1-5", torch_dtype=torch.float32, use_safetensors=True)
pipeline = pipeline.to("cuda")

# remove the nsfw warning to not get black images
pipeline.safety_checker = lambda images, **kwargs: (images, [False] * len(images))

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


model_index.json:   0%|          | 0.00/541 [00:00<?, ?B/s]

Fetching 15 files:   0%|          | 0/15 [00:00<?, ?it/s]

safety_checker/config.json:   0%|          | 0.00/4.72k [00:00<?, ?B/s]

tokenizer/special_tokens_map.json:   0%|          | 0.00/472 [00:00<?, ?B/s]

...

model.safetensors:   0%|          | 0.00/492M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.22G [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/335M [00:00<?, ?B/s]

diffusion_pytorch_model.safetensors:   0%|          | 0.00/3.44G [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

# Iteratively generating images for each image text row

In [15]:
folder_path = "../../Dataset1/Images" # relative folder path for saving the images
os.chdir('/content/drive/My Drive/Big-Foot/Assignment_2/Scripts/task5') # repeating chdir code to be sure

os.makedirs(folder_path, exist_ok=True) # make path if it does not exists

# iterating over each row to generate an image for the image text at each index
for index, row in df.iterrows():
  #if index < 4832: # skipping rows until where the runtime disconnected
    #continue
  prompt = row['Image Text'] # # setting the image prompt
  image = pipeline(prompt, num_inference_steps=50).images[0] # generating the image
  image_filename = f"image_{index}.png"
  image_path = os.path.join(folder_path, image_filename) # creating the path
  image.save(image_path)
  # saving the local image url to a image url column
  df.at[index, 'Image URL'] = image_path

  0%|          | 0/50 [00:00<?, ?it/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (79 > 77). Running this sequence through the model will result in indexing errors
The following part of your input was truncated because CLIP can only handle sequences up to 77 tokens: ['heard it']


  0%|          | 0/50 [00:00<?, ?it/s]

The following part of your input was truncated because CLIP can only handle sequences up to 77 tokens: ['1 0 0 0 am good light colder and']


  0%|          | 0/50 [00:00<?, ?it/s]

...

The following part of your input was truncated because CLIP can only handle sequences up to 77 tokens: ['manive seen moose deer elk steers skunks']


  0%|          | 0/50 [00:00<?, ?it/s]

The following part of your input was truncated because CLIP can only handle sequences up to 77 tokens: ['places there were some washouts and small creeks']


  0%|          | 0/50 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

# Creating Image URL column with relative local url path to each image

In [20]:
folder_path = "../../Dataset1/Images"

# set the 'Image URL' column based on the folder path and image index
df['Image URL'] = df.index.map(lambda image_index: f"{folder_path}/image_{image_index}.png")

print(df)

save_path = "../../Dataset1"
# saving
df.to_csv(f"{save_path}/reports_v2_task5.tsv", sep='\t', index=False)


        Report Type     Id    Class                Submitted Date  \
0            Report  13038  Class A  Saturday, November 12, 2005.   
1            Report   8792  Class B       Thursday, June 3, 2004.   
2            Report   1255  Class B     Tuesday, October 5, 1999.   
3     Media Article    658      NaN   Wednesday, January 23, 2013   
4            Report  11616  Class B          Friday, May 6, 2005.   
...             ...    ...      ...                           ...   
5462         Report   1411  Class A    Tuesday, January 23, 2001.   
5463  Media Article     59      NaN      Wednesday, June 18, 1980   
5464         Report  14714  Class A         Friday, May 19, 2006.   
5465         Report  12884  Class A    Tuesday, October 25, 2005.   
5466         Report    798  Class B        Monday, June 26, 2000.   

                                               Headline  Year  Season  \
0     Snowmobiler has encounter in deep snow near Po...  2004  Winter   
1     Four nocturnal hike